# Image Encoding with FRQI: 2x2 image

In this demo, you will learn how to encode a $2\times 2$ image into a quantum computer. 

As basis of our study, we used the [Flexible Representation of Quantum Images (FRQI)](https://doi.org/10.1007/s11128-010-0177-y) method and adapted the standard implementation MCRY- with our MARY-implementation.

**This notebook is meant to support the understanding of our paper [Improved FRQI on superconducting processors and its restrictions in the NISQ era](https://doi.org/10.1007/s11128-023-03838-0).**

<div style="overflow: auto;">
    <img src="https://www.itwm.fraunhofer.de/content/businesscards/ITWM/bv/alexander_geng/jcr:content/businesscard/image.img.1col.jpg/1660740872670/230x230-itwm-bv-geng-alexander.jpg" alt="Landscape" width="100" style="float: left; margin-right: 10px;"/>
    <p style="margin: 0;"> _________________________________</p>
    <p style="margin: 0;">Author: Alexander Geng.</p>
    <p style="margin: 0;">Published: Decenber 1, 2023. </p>
    <p style="margin: 0;">Last updated: December 1, 2023. </p>
    <p style="margin: 0;"> _________________________________</p>
</div>

### Import required packages

In [ ]:
from math import pi, sqrt, acos, sin
import numpy as np
from pprint import pprint # pretty printer
import matplotlib.pyplot as plt

import qiskit as qk
from qiskit import Aer,execute, transpile
# from qiskit import IBMQ
from qiskit_ibm_provider import least_busy
from qiskit.visualization import plot_histogram, plot_bloch_multivector

### Difference calculator

In [ ]:
# Define a function named 'calc_difference' that takes an 'image' as input
def calc_difference(image):
    # Initialize a variable 'summe' to keep track of the sum of differences
    summe = 0
    
    # Iterate through the range of the length of the 'image'
    for i in range(len(image)):
        # Calculate the absolute difference between elements of 'image' and 'input_image'
        diff = abs(image[i] - input_image[i])
        
        # Add the absolute difference to the 'summe' variable
        summe = summe + diff
    
    # Calculate the percentage difference using the obtained 'summe' value
    # Normalize the sum by dividing by the length of the 'image' and then by 2.55
    prozent = summe / len(image) / 2.55
    
    # Round the 'prozent' value to 2 decimal places
    prozent = prozent.round(2)
    
    # Return the calculated percentage difference
    return prozent


### Function for visualization

In [ ]:
# Define a function 'plot_image' that takes four arguments: 'vector', 'im_w', 'im_h', 'normalized'
def plot_image(vector, im_w, im_h, normalized): 
    # Reshape the 'vector' into a 2D array of shape (im_h, im_w)
    array = np.reshape(vector, [im_h, im_w])  # Transform vector to array
    
    # Create a new figure for plotting
    plt.figure(figsize=(6, 6))
    
    # Check if the 'normalized' flag is set to False
    if normalized == False:
        # Plot the image using grayscale colormap, set minimum and maximum values of the colormap (0-255), and origin as 'upper'
        im = plt.imshow(array, cmap='gray', vmin=0, vmax=255, origin='upper')
    else:
        # Plot the image using grayscale colormap, setting the minimum and maximum values based on the array, and origin as 'upper'
        im = plt.imshow(array, cmap='gray', vmin=np.min(array), vmax=np.max(array), origin='upper')
    
    # Get the current axes
    ax = plt.gca()
    
    # Set major ticks for x and y axes using numpy.arange for regular intervals
    ax.set_xticks(np.arange(0, im_w, 1))
    ax.set_yticks(np.arange(0, im_h, 1))

    # Set labels for major ticks
    ax.set_xticklabels(np.arange(0, im_w, 1))
    ax.set_yticklabels(np.arange(0, im_h, 1))

    # Set minor ticks for fine gridlines
    ax.set_xticks(np.arange(-.5, im_w, 1), minor=True)
    ax.set_yticks(np.arange(-.5, im_h, 1), minor=True)
    
    # Set a title for the plot showing various statistics of the image array
    ax.set_title('Min=' + str(round(np.min(array), 4)) +
                 ', Max=' + str(round(np.max(array), 4)) +
                 ', Mean=' + str(round(np.mean(array), 4)) +
                 ', Std=' + str(round(np.std(array), 4)) +
                 ', Size=' + str((im_h, im_w)), fontsize=14)

    # Add gridlines based on minor ticks
    ax.grid(which='minor', color='k', linestyle='-', linewidth=2)
    
    # Loop through each pixel in the array for displaying pixel values as text on the plot
    for i in range(im_h):
        for j in range(im_w):
            # Choose text color based on pixel intensity
            if array[i, j] < 128:
                color = "w"  # White color for darker pixels
            else:
                color = "k"  # Black color for lighter pixels
            
            # Add text annotations for pixel values on the plot
            ax.text(j, i, array[i, j], ha="center", va="center", color=color, fontsize=30)


### Simulator specifications

In [ ]:
num_shots=8192 # Number of shots for the simulator or real backend
backend_state = Aer.get_backend('statevector_simulator')
backend_sim = Aer.get_backend('qasm_simulator')

## Input image and pre-processing

In [ ]:
input_image=np.array([10,85,170,255])
image = input_image.astype('float64')

# Normalization to the intervall 0~pi/2
image /= 255.0
angles=image*pi/2
print(angles)

In [ ]:
plot_image(input_image, im_w=2, im_h=2, normalized=False) # Visualization of the image with pixel values

In [ ]:
def inverse_normalization(angles):
    'Define the inverse operation for reconstructing the pixel values from angles'
    
    # Convert the 'angles' into a NumPy array
    img = np.array(angles)
    
    # Scale the values by 255 and then by 2/pi to reverse normalization
    img *= 255  # Scaling values by 255
    img *= 2 / pi  # Scaling values by 2/pi
    
    # Convert the resulting values to integers
    img = img.astype(int)
    
    # Return the resulting image (pixel values after the inverse normalization)
    return img


## Create Circuits
The standard implementation of FRQI would use multi-controlled $R_y$-gates. They produce a lost of CX-gates and require an entanglement of all qubits. We adapted this process with the MARY-implementation similar to [Co et al.](https://github.com/shedka/citiesatnight)

In [ ]:
def mary(circ, angle, t, c0, c1):
    circ.ry(angle/4,t)
    circ.cx(c0, t)
    circ.ry(-angle/4,t)
    circ.cx(c1, t)
    circ.ry(angle/4,t)
    circ.cx(c0, t)
    circ.ry(-angle/4,t)
    circ.cx(c1, t)

In [ ]:
N=1
m=2**N
pos_qubits=2*N

## Investigation of the operator
Before we use the circuits for the encoding, we want to investigate the operators, we create with the circuits. For that we get rid of the measurements at the end of the circuits and use the command `array_to_latex` for showing the matrix of the operator.

In [ ]:
from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister
import time
def create_circ(method, circs, angles, measure_bool):
    start = time.time()
    pos= QuantumRegister(pos_qubits,'pos')
    color=QuantumRegister(1,'color')
    circ=QuantumCircuit(pos,color)
    circ.h(range(pos_qubits))
    i=0
    for ang in angles:

        if i!=0:
            # to make sure we are transforming the correct vector, need to NOT certain qubits
            circ.x(pos[1])
            for j in range(1,pos_qubits):
                if(i%2**j==0):
                    #print(pos[-j-1])
                    circ.x(pos[-j-1])
        
        if method=='mcry':
            control_qubits=[j for j in range(pos_qubits)]
            circ.mcry(2*ang,q_controls=pos[control_qubits], q_target=color[0],q_ancillae=None, mode='noancilla')
        elif method=='mary':
            mary(circ, 2*ang ,t=2, c0=1, c1=0)

        i += 1

        circ.barrier()
    circ=circ.reverse_bits()
    if measure_bool==True:
        circ.measure_all()
    else:
        print('No measurements')
    end = time.time()
    print('Time needed: {:5.3f}s'.format(end-start), 'for creating circuit via', method)
    circs.append(circ)

In [ ]:
test_angle=[2*pi/7]
circs=[]
create_circ('mcry', circs, test_angle, measure_bool=False)
create_circ('mary', circs, test_angle, measure_bool=False)

In [ ]:
circs[0].draw(output='mpl')

In [ ]:
circs[1].draw(output='mpl')

In [ ]:
# !pip3 install git+https://github.com/qiskit-community/qiskit-textbook.git#subdirectory=qiskit-textbook-src

In [ ]:
import qiskit.quantum_info as qi
from qiskit_textbook.tools import array_to_latex
op_mcry = qi.Operator(circs[0])
array_to_latex(op_mcry.data, pretext="\\text{MCRY = }\n", display_output=True)
op_mary = qi.Operator(circs[1])
array_to_latex(op_mary.data, pretext="\\text{MARY = }\n", display_output=True)
array_to_latex((op_mary-op_mcry).data, pretext="\\text{Difference = }\n", display_output=True)

### Both operator do the the same. So let us use them for the encoding:

In [ ]:
circs=[]
create_circ('mcry', circs, angles, measure_bool=True)
create_circ('mary', circs, angles, measure_bool=True)

In [ ]:
circs[0].draw(output='mpl')

In [ ]:
circs[1].draw(output='mpl')

In [ ]:
from qiskit.tools.monitor import job_monitor
results=[]
counts=[]
outputs=[]
def execute_sim(circs, numOfShots, backend, sim_bool):
    '''
    Execute the encoding and append the result to a list
    '''
    print('Used backend: ', backend)
#     job = backend.run(transpile(circs, backend), shots=numOfShots)
    job = execute(circs, backend, shots=numOfShots)
    print('Job_ID: ', job.job_id())
    result = job.result()
    if sim_bool == False:
        print(job_monitor(job))
        # timecalculation(job)
    else:
        execution_time = result.time_taken # Calculate time
        print('Execution time: ', str(round(execution_time,2))+'s')
    
    counts_job = result.get_counts()
    results.append(result)
    counts.append(counts_job)

In [ ]:
backend_names = []
execute_sim(circs, numOfShots = num_shots, backend = backend_sim, sim_bool = True)
backend_names.append(backend_sim.name())

In [ ]:
circ_names=['MCRY', 'MARY']

In [ ]:
def probs(counts, num_shots, num_ancilla, num_pos_qubits):
    '''
    Function to convert the probabilities into angles
    '''
    states=[]
    for k in range(2**(2*N+num_ancilla+1)):
        k_bin=bin(k)[2:].zfill(2*N+num_ancilla+1)
        states.append(k_bin)

    probs=[]
    for state in states:
        if (state in counts):
            prob=counts[state]/num_shots
            probs.append(prob)
        else:
            prob=0
            probs.append(prob)

    angles=[]
    for i in range(len(image)):
        # First part for position qubits,then ancilla and then color qubit
        zero=int(format(i, '0'+str(num_pos_qubits)+'b') +'0',2) 
        one=int(format(i, '0'+str(num_pos_qubits)+'b')  +'1',2)
        try:
            zero_prob=probs[zero]/(probs[zero]+probs[one])
            angles.append(acos(sqrt(zero_prob)))
        except:
            angles.append(0)    
    return angles, probs

### For the paper repeat the execution 42 times

In [ ]:
print('Input_image: ', input_image)
for a in range(42):
    execute_sim(circs, numOfShots=num_shots, backend=backend_sim, sim_bool=True)
    for i in range(2):
        num_ancilla=circs[i].num_qubits-(pos_qubits+1)
        #print('Number of ancillas: '+ str(num_ancilla))
        new_angles,prob = probs(counts[a][i], num_shots, num_ancilla=num_ancilla, num_pos_qubits=pos_qubits)
        image_out=inverse_normalization(new_angles)
        diff=calc_difference(image_out)
        print('Output_image with backend '+backend_names[0]+' and method '+circ_names[i]+':', image_out, ' --> ', diff, '%')
        outputs.append(image_out)

### Reconstructing the image and show difference to input image

In [ ]:
print('Input_image: ', input_image)
for i in range(2):
    num_ancilla=circs[i].num_qubits-(pos_qubits+1)
    #print('Number of ancillas: '+ str(num_ancilla))
    new_angles,prob = probs(counts[0][i], num_shots, num_ancilla=num_ancilla, num_pos_qubits=pos_qubits)
    image_out=inverse_normalization(new_angles)
    diff=calc_difference(image_out)
    print('Output_image with backend '+backend_names[0]+' and method '+circ_names[i]+':', image_out, ' --> ', diff, '%')
    outputs.append(image_out)

In [ ]:
plot_histogram(counts[0], figsize=(20,5), legend=['MCRY', 'MARY'])

# Real Machine

### Check only for active backends, which have enough qubits

In [ ]:
from pprint import pprint # pretty printer
from qiskit_ibm_provider import IBMProvider
from qiskit_ibm_provider import least_busy

token=''# Insert your token here
IBMProvider.save_account(token, overwrite=True)
provider = IBMProvider()

def backend_filter_num_circuit(b):
    return b.configuration().n_qubits >= 2*N+1 and not b.configuration().simulator and b.status().operational==True and b.status().status_msg=='active'
backends_list=provider.backends(filters=backend_filter_num_circuit)

# display current supported backends
pprint(backends_list)

In [ ]:
# Just take the least_busy backend
backend_real=least_busy(provider.backends(filters=backend_filter_num_circuit))
print(backend_real)

### Transpilation
To get a feeling about the complexity of the circuits, it is always advisable to track the circuit depth and number of quantum gates before running the circuit on the real backends

In [ ]:
from qiskit import transpile
for i in range(2):
    print('Used method:', circ_names[i])
    print('Circuit_depth simulator:', circs[i].depth())
    print('Circuit_depth simulator:', circs[i].count_ops())
    new_circ=transpile(circs[i], backend_real)
    print('Circuit_depth '+backend_real.name, new_circ.depth())
    print('Circuit_depth '+backend_real.name, new_circ.count_ops())

In [ ]:
def timecalculation(job_real):
    '''
    Printing the time the job needed to execute, validate, create, and queue
    You can also just track the job id and restore the time from the result of the job
    '''
    result_real = job_real.result()
    execution_time = result_real.time_taken # Actually runtime that is needed to perform the circuit

    times=job_real.time_per_step()

    duration_creation = times['CREATED']-times['CREATING'] # Time that is needed for creation of the circuit                       
    duration_creation_in_s = duration_creation.total_seconds()  
    duration_validation = times['VALIDATED']-times['VALIDATING']  # Validation time                    
    duration_validation_in_s = duration_validation.total_seconds()
    duration_queue = times['RUNNING']-times['VALIDATED'] #Time to wait for the execution                        
    duration_queue_in_s = duration_queue.total_seconds()
    duration_execution = times['COMPLETED']-times['RUNNING'] # Execution time with postprocessing like storing the data                        
    duration_execution_in_s = duration_execution.total_seconds()
    print('Code was executed on:', times['RUNNING'])
    print('Job ID:',job_real.job_id())
    
    print('Execution time: ', str(execution_time)+'s')
    print('Time for Creation: ',str(duration_creation_in_s)+'s')
    print('Time for Validation: ',str(duration_validation_in_s)+'s')
    if duration_queue_in_s>60:
        duration_queue_in_min = int(divmod(duration_queue_in_s, 60)[0])
        duration_queue_s = int(divmod(duration_queue_in_s, 60)[1])
        print('Time in Queue: ',str(duration_queue_in_min)+'m'+str(duration_queue_s)+'s')
    else:
        print('Time in Queue: ',str(duration_queue_in_s)+'s')
    print('Time for Execution with postprocessing: ',str(duration_execution_in_s)+'s')

In [ ]:
# Execution on the real backend
execute_sim(circs, numOfShots=num_shots, backend=backend_real, sim_bool=False)

In [ ]:
print('Input_image: ', input_image)
for i in range(2):
    num_ancilla=circs[i].num_qubits-(pos_qubits+1)
    #print('Number of ancillas: '+ str(num_ancilla))
    new_angles,prob = probs(counts[-1][i], num_shots, num_ancilla=num_ancilla, num_pos_qubits=pos_qubits)
    image_out=inverse_normalization(new_angles)
    diff=calc_difference(image_out)
    print('Output_image with backend '+backend_names[0]+' and method '+circ_names[i]+':', image_out, ' --> ', diff, '%')
    outputs.append(image_out)

In [ ]:
plot_histogram([counts[0][0], counts[0][0],counts[-1][0],counts[-1][1]], figsize=(20,5), legend=['MCRY_sim', 'MARY_sim', 'MCRY_real', 'MARY_real'])

In [ ]:
plot_image(outputs[-2], im_w=2, im_h=2, normalized=False) # Visualization of the image with pixel values

In [ ]:
plot_image(outputs[-1], im_w=2, im_h=2, normalized=False) # Visualization of the image with pixel values

# Measurement error mitigation

We give here just a rough idea about measurement error mitigation that we used in our paper [Improved FRQI on superconducting processors and its restrictions in the NISQ era](https://doi.org/10.1007/s11128-023-03838-0). Currently, there are a lot of other techniques to minimize or correct errors, which we don't cover here.

In [ ]:
# !pip3 install qiskit-ignis

In [ ]:
from qiskit.ignis.mitigation.measurement import (complete_meas_cal,CompleteMeasFitter)
qr = qk.QuantumRegister(3)
meas_calibs, state_labels = complete_meas_cal(qr=qr, circlabel='mcal')
for circuit in meas_calibs:
    print('Circuit',circuit.name)
    print(circuit)
    print()

In [ ]:
from qiskit.providers.aer.noise import NoiseModel
from qiskit.providers.aer.noise.errors import pauli_error, depolarizing_error

def get_noise(p_meas,p_gate):
    
    '''
    Choose an arbitrary noise model according to your wishes.
    '''

    error_meas = pauli_error([('X',p_meas), ('I', 1 - p_meas)])
    error_gate1 = depolarizing_error(p_gate, 1)
    error_gate2 = error_gate1.tensor(error_gate1)

    noise_model = NoiseModel()
    noise_model.add_all_qubit_quantum_error(error_meas, "measure") # measurement error is applied to measurements
    noise_model.add_all_qubit_quantum_error(error_gate1, ["x"]) # single qubit gate error is applied to x gates
    noise_model.add_all_qubit_quantum_error(error_gate2, ["cx"]) # two qubit gate error is applied to cx gates
        
    return noise_model
noise_model = get_noise(0.1,0.1)

In [ ]:
counts_own=[]
for result in results[43:]:
    job = execute(meas_calibs, backend=backend_sim, shots=8192, noise_model=noise_model)
    cal_results = job.result()
    meas_fitter = CompleteMeasFitter(cal_results, state_labels, circlabel='mcal')
    meas_filter = meas_fitter.filter
    # Results with mitigation on the real output
    mitigated_results = meas_filter.apply(result)
    mitigated_counts = mitigated_results.get_counts()
    counts_own.append(mitigated_counts)

In [ ]:
plot_histogram(counts_own[0], figsize=(20,5), legend=['MCRY', 'MARY'])

In [ ]:
print('Input_image: ', input_image)
for i in range(2):
    num_ancilla=circs[i].num_qubits-(pos_qubits+1)
    #print('Number of ancillas: '+ str(num_ancilla))
    new_angles,prob = probs(counts_own[0][i], num_shots, num_ancilla=num_ancilla, num_pos_qubits=pos_qubits)
    image_out=inverse_normalization(new_angles)
    diff=calc_difference(image_out)
    print('Output_image with backend '+backend_names[0]+' and method '+circ_names[i]+':', image_out, ' --> ', diff, '%')
    outputs.append(image_out)

In [ ]:
def plot_images(vectors, im_w, im_h, normalized, abs_diff, font_pixels, font_title, font_axes):
    arrays=[]
    for vector in vectors:
        array=np.reshape(vector,[im_h,im_w])#Transform vector to array
        arrays.append(array)
    
    fig = plt.figure(figsize=(len(vectors)*7, len(vectors)*7))
    
    
    sub1 = fig.add_subplot(1,3,1) # instead of plt.subplot(2, 2, 1)
    sub2 = fig.add_subplot(1,3,2) # instead of plt.subplot(2, 2, 1)
    
    
    if normalized==False:
        sub1.imshow(arrays[0], cmap='gray', vmin=0, vmax=255, origin='upper')         
        sub2.imshow(arrays[1], cmap='gray', vmin=0, vmax=255, origin='upper')
    else:
        sub1.imshow(array, cmap='gray', vmin=np.min(arrays[0]), vmax=np.max(arrays[0]), origin='upper')
        sub2.imshow(array, cmap='gray', vmin=np.min(arrays[1]), vmax=np.max(arrays[1]), origin='upper')
    
    
    
    # Major ticks
    sub1.set_xticks(np.arange(0, im_w, 1))
    sub1.set_yticks(np.arange(0, im_h, 1))

    # Labels for major ticks
    sub1.set_xticklabels(np.arange(0, im_w, 1), fontsize=font_axes)
    sub1.set_yticklabels(np.arange(0, im_h, 1), fontsize=font_axes)

    # Minor ticks
    sub1.set_xticks(np.arange(-.5, im_w, 1), minor=True)
    sub1.set_yticks(np.arange(-.5, im_h, 1), minor=True)
    
    sub1.set_title('Image_in \nMin='+str(round(np.min(arrays[0]),4))+', Max='+str(round(np.max(arrays[0]),4))+', Mean='+str(round(np.mean(arrays[0]),4))+', Std='+str(round(np.std(arrays[0]),4))+', Size=' + str((im_h,im_w)), fontsize=font_title)
    for i in range(im_h):
        for j in range(im_w):
            if arrays[0][i,j]<128:
                color="w"
            else:
                color="k"
            sub1.text(j, i, arrays[0][i, j], ha="center", va="center", color=color, fontsize=font_pixels)
    
    # Major ticks
    sub2.set_xticks(np.arange(0, im_w, 1))
    sub2.set_yticks(np.arange(0, im_h, 1))

    # Labels for major ticks
    sub2.set_xticklabels(np.arange(0, im_w, 1), fontsize=font_axes)
    sub2.set_yticklabels(np.arange(0, im_h, 1), fontsize=font_axes)

    # Minor ticks
    sub2.set_xticks(np.arange(-.5, im_w, 1), minor=True)
    sub2.set_yticks(np.arange(-.5, im_h, 1), minor=True)
    
    sub2.set_title('Image_out \nMin='+str(round(np.min(arrays[1]),4))+', Max='+str(round(np.max(arrays[1]),4))+', Mean='+str(round(np.mean(arrays[1]),4))+', Std='+str(round(np.std(arrays[1]),4))+', Size=' + str((im_h,im_w)), fontsize=font_title)
    for i in range(im_h):
        for j in range(im_w):
            if arrays[1][i,j]<128:
                color="w"
            else:
                color="k"
            sub2.text(j, i, arrays[1][i, j], ha="center", va="center", color=color, fontsize=font_pixels)
            
    ##Abs_Diff image
    if abs_diff==True:
        sub3 = fig.add_subplot(1,3,3)
        array_diff=abs(arrays[1]-arrays[0])
        sub3.imshow(array_diff, cmap='gray', vmin=0, vmax=255, origin='upper')
         # Major ticks
        sub3.set_xticks(np.arange(0, im_w, 1))
        sub3.set_yticks(np.arange(0, im_h, 1))

        # Labels for major ticks
        sub3.set_xticklabels(np.arange(0, im_w, 1), fontsize=font_axes)
        sub3.set_yticklabels(np.arange(0, im_h, 1), fontsize=font_axes)

        # Minor ticks
        sub3.set_xticks(np.arange(-.5, im_w, 1), minor=True)
        sub3.set_yticks(np.arange(-.5, im_h, 1), minor=True)
        sub3.set_title('Abs_diff(image_in, image_out) \nMin='+str(round(np.min(array_diff),4))+', Max='+str(round(np.max(array_diff),4))+', Mean='+str(round(np.mean(array_diff),4))+', Std='+str(round(np.std(array_diff),4))+', Size=' + str((im_h,im_w)), fontsize=font_title)
        for i in range(im_h):
            for j in range(im_w):
                if array_diff[i,j]<128:
                    color="w"
                else:
                    color="k"
                sub3.text(j, i, array_diff[i, j], ha="center", va="center", color=color, fontsize=font_pixels)
    
    plt.subplots_adjust(left=None, bottom=None, right=2, top=None, wspace=None, hspace=None)
    plt.show()

### MCRY mitigated

In [ ]:
vectors=[input_image, outputs[-2]]
plot_images(vectors, im_w=m, im_h=m, normalized=False, abs_diff=True, font_pixels=30, font_title=20, font_axes=25)

### MARY mitigated

In [ ]:
vectors=[input_image, outputs[-1]]
plot_images(vectors, im_w=m, im_h=m, normalized=False, abs_diff=True, font_pixels=30, font_title=20, font_axes=25)

    
**Note:**
<div class="alert alert-block alert-success">
    This form of measurement error mitigation is primarily intended for demonstration purposes and may not consistently yield improved results.
<div>    

In [78]:
# qiskit version table
import qiskit.tools.jupyter
%qiskit_version_table

In [79]:
pip list

Package                           Version
--------------------------------- ---------------
aiofiles                          22.1.0
aiosqlite                         0.19.0
alembic                           1.10.4
altair                            4.2.0
ansiwrap                          0.8.4
antlr4-python3-runtime            4.13.1
anyio                             3.6.2
appdirs                           1.4.4
argon2-cffi                       21.3.0
argon2-cffi-bindings              21.2.0
arrow                             1.2.3
asttokens                         2.2.0
async-generator                   1.10
attrs                             22.2.0
autograd                          1.6.2
autopep8                          2.0.2
autoray                           0.6.7
Babel                             2.11.0
backcall                          0.2.0
backports.functools-lru-cache     1.6.4
beautifulsoup4                    4.11.1
bleach                            5.0.1
blinker             

In [ ]:
# !pip3 freeze > requirements.txt

In [ ]:
# !conda env export > environment.yml

References
==========
\[1\] Geng, Alexander, et al. *Hybrid quantum transfer learning for crack image classification on NISQ hardware.* arXiv preprint arXiv:2307.16723 (2023).

\[2\] Geng, Alexander, et al. *Improved FRQI on superconducting processors and its restrictions in the NISQ era.* Quantum Information Processing 22.2 (2023): 104.

\[3\] Geng, Alexander, et al. *A hybrid quantum image edge detector for the NISQ era." Quantum Machine Intelligence 4.2 (2022): 15.